# Geopy
https://geopy.readthedocs.io/en/stable/

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from plantclef.spark import get_spark

spark = get_spark()
display(spark)

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/04/16 12:34:05 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
25/04/16 12:34:05 WARN SparkConf: Note that spark.local.dir will be overridden by the value set by the cluster manager (via SPARK_LOCAL_DIRS in mesos/standalone/kubernetes and LOCAL_DIRS in YARN).
25/04/16 12:34:06 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


In [3]:
import os
from pathlib import Path

# Set the root directory to your home directory
root = Path(os.path.expanduser("~"))
! date

Wed Apr 16 12:34:09 PM EDT 2025


In [4]:
# path and dataset names
data_path = f"{root}/p-dsgt_clef2025-0/shared/plantclef/data/parquet"

# define the path to the train and test parquet files
train_path = f"{data_path}/train"

# read the parquet files into a spark DataFrame
train_df = spark.read.parquet(train_path)

# show the data
train_df.printSchema()
train_df.show(n=5)

root
 |-- image_name: string (nullable = true)
 |-- path: string (nullable = true)
 |-- data: binary (nullable = true)
 |-- organ: string (nullable = true)
 |-- species_id: integer (nullable = true)
 |-- obs_id: long (nullable = true)
 |-- license: string (nullable = true)
 |-- partner: string (nullable = true)
 |-- author: string (nullable = true)
 |-- altitude: double (nullable = true)
 |-- latitude: double (nullable = true)
 |-- longitude: double (nullable = true)
 |-- gbif_species_id: string (nullable = true)
 |-- species: string (nullable = true)
 |-- genus: string (nullable = true)
 |-- family: string (nullable = true)
 |-- dataset: string (nullable = true)
 |-- publisher: string (nullable = true)
 |-- references: string (nullable = true)
 |-- url: string (nullable = true)
 |-- learn_tag: string (nullable = true)
 |-- image_backup_url: string (nullable = true)



+--------------------+--------------------+--------------------+-----+----------+----------+--------------------+-------+----------------+--------+-----------------+------------------+---------------+--------------------+-------------+----------+--------+-----------+--------------------+--------------------+---------+--------------------+
|          image_name|                path|                data|organ|species_id|    obs_id|             license|partner|          author|altitude|         latitude|         longitude|gbif_species_id|             species|        genus|    family| dataset|  publisher|          references|                 url|learn_tag|    image_backup_url|
+--------------------+--------------------+--------------------+-----+----------+----------+--------------------+-------+----------------+--------+-----------------+------------------+---------------+--------------------+-------------+----------+--------+-----------+--------------------+--------------------+---------

In [5]:
# count number of NULL latitude and longitude data
null_latitude_count = train_df.filter(train_df.latitude.isNull()).count()
null_longitude_count = train_df.filter(train_df.longitude.isNull()).count()
print(f"Number of NULL latitude values: {null_latitude_count}")
print(f"Number of NULL longitude values: {null_longitude_count}")

Number of NULL latitude values: 702608
Number of NULL longitude values: 702592


In [6]:
# filter out the rows with NULL latitude and longitude
filtered_df = train_df.filter(
    train_df.latitude.isNotNull() & train_df.longitude.isNotNull()
)
# groupby species_id and average the latitude and longitude of each species
grouped_df = filtered_df.groupBy("species_id").agg(
    {"latitude": "avg", "longitude": "avg"}
)
# rename the columns
grouped_df = grouped_df.withColumnRenamed("avg(latitude)", "avg_latitude")
grouped_df = grouped_df.withColumnRenamed("avg(longitude)", "avg_longitude")
# show the first 5 rows
grouped_df.show(n=5)

+----------+------------------+------------------+
|species_id|      avg_latitude|     avg_longitude|
+----------+------------------+------------------+
|   1737493| 46.36360531186132| 5.639311481005929|
|   1363733| 42.12276511772893| 6.716418020291944|
|   1743681|  43.9162545329139|3.4286095476539384|
|   1359356|38.116486922794394| 8.350581385996264|
|   1741934|         42.625339|         25.145366|
+----------+------------------+------------------+
only showing top 5 rows



In [7]:
# count the number of unique species from the grouped DataFrame
unique_species_count = grouped_df.select("species_id").count()
print(f"Number of unique species: {unique_species_count}")

Number of unique species: 6208


In [8]:
import folium


def plot_map(df, col_latitude: str, col_longitude: str):
    # plot the grouped_df DataFrame
    pandas_df = df.toPandas()

    # Create a folium map centered around southwestern Europe
    map_center = [44.0, 4.0]  # roughly southern France
    m = folium.Map(location=map_center, zoom_start=5, tiles="OpenStreetMap")

    # Add markers for each species
    for _, row in pandas_df.iterrows():
        folium.CircleMarker(
            location=[row[col_latitude], row[col_longitude]],
            radius=4,
            popup=str(row["species_id"]),
            color="green",
            fill=True,
            fill_opacity=0.6,
        ).add_to(m)

    # Save or display map
    # m.save("species_map.html")
    return m

### Euclidean distance

In [10]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window

# define the reference point (Southern France / SW Europe)
ref_lat = 44.0
ref_lon = 4.0

# filter out null latitude and longitude
filtered_df = train_df.filter(
    train_df.latitude.isNotNull() & train_df.longitude.isNotNull()
)

# compute squared Euclidean distance to map_center
df_with_distance = filtered_df.withColumn(
    "distance",
    F.pow(F.col("latitude") - F.lit(ref_lat), 2)
    + F.pow(F.col("longitude") - F.lit(ref_lon), 2),
)

# define window by species_id, ordering by distance
window_spec = Window.partitionBy("species_id").orderBy(F.col("distance").asc())

# Get closest point per species
closest_points_df = df_with_distance.withColumn(
    "rank", F.row_number().over(window_spec)
).filter(F.col("rank") == 1)

# Select final columns
final_df = closest_points_df.select("species_id", "latitude", "longitude")
final_df.show(n=5)

+----------+-----------------+-----------------+
|species_id|         latitude|        longitude|
+----------+-----------------+-----------------+
|   1355868|43.95999191666667|        3.9117065|
|   1355869|     44.056356625|3.862885908333333|
|   1355870|       43.8347442|        3.8857002|
|   1355871|        44.050021|          3.85021|
|   1355872|        44.046747|4.105631972222222|
+----------+-----------------+-----------------+
only showing top 5 rows



In [11]:
map = plot_map(final_df, col_latitude="latitude", col_longitude="longitude")
map

### species in France

In [41]:
import geopandas as gpd
from shapely.geometry import Point


def load_country_data():
    # load the shapefile for France
    shapefile_path = os.path.expanduser(
        "~/p-dsgt_clef2025-0/shared/plantclef/data/ne_110m_admin_0_countries/ne_110m_admin_0_countries.shp"
    )
    world = gpd.read_file(shapefile_path)
    return world


def get_country_geometry(country_name: list[str]):
    # load the country data
    world = load_country_data()

    # filter the DataFrame for the specified country
    countries = world[world["NAME"].isin(country_name)]
    return countries


def get_country_list(countries):
    # convert the Spark DataFrame to Pandas DataFrame
    pandas_df = final_df.toPandas()

    # convert your coordinates DataFrame to GeoDataFrame
    pandas_df["geometry"] = pandas_df.apply(
        lambda row: Point(row["longitude"], row["latitude"]), axis=1
    )
    geo_df = gpd.GeoDataFrame(pandas_df, geometry="geometry", crs="EPSG:4326")

    # check if each point is within France's borders
    species_in_countries = geo_df[geo_df.geometry.within(countries.iloc[0].geometry)]
    return species_in_countries


country_list = ["France", "Spain", "Italy", "Switzerland"]
countries = get_country_geometry(country_list)
species_in_countries = get_country_list(countries)

print(
    f"Found {len(species_in_countries)} species located in {', '.join(country_list)} based on coordinates."
)
print(species_in_countries.head())

Found 4981 species located in France, Spain, Italy, Switzerland based on coordinates.
   species_id   latitude  longitude                  geometry
0     1355868  43.959992   3.911707  POINT (3.91171 43.95999)
1     1355869  44.056357   3.862886  POINT (3.86289 44.05636)
2     1355870  43.834744   3.885700   POINT (3.8857 43.83474)
3     1355871  44.050021   3.850210  POINT (3.85021 44.05002)
4     1355872  44.046747   4.105632  POINT (4.10563 44.04675)


In [ ]:
# France
france = get_country_geometry(["France"])
france_df = get_country_list(france)
france_sp = france_df["species_id"].tolist()
print(f"Found {len(france_df)} species located in France.")
# France
spain = get_country_geometry(["Spain"])
spain_df = get_country_list(spain)
spain_sp = france_df["species_id"].tolist()
print(f"Found {len(spain_df)} species located in Spain.")

Found 4981 species located in France.
Found 447 species located in Spain.


In [ ]:
# get the intersection of the two lists
intersection = set(france_sp).intersection(set(spain_sp))
print(f"Found {len(intersection)} species located in both France and Spain.")

Found 4981 species located in both France and Spain.


In [42]:
import pandas as pd


# save the intersection to a CSV file
intersection_df = pd.DataFrame(intersection, columns=["species_id"])
file_path = "~/p-dsgt_clef2025-0/shared/plantclef/data/france_geodata_species.csv"
intersection_df.to_csv(file_path, index=False)